In [24]:
from io import BytesIO
from zipfile import ZipFile
from urllib.request import urlopen
import geopandas as gpd
from io import StringIO
# or: requests.get(url).content
from shapely.geometry import Point, LineString

resp = urlopen("https://developer.trimet.org/gis/data/tm_boundary.zip")
myzip = ZipFile(BytesIO(resp.read()))
myzip.extractall('gis/export/')

In [2]:
resp = urlopen("https://developer.trimet.org/schedule/gtfs.zip")
myzip = ZipFile(BytesIO(resp.read()))
myzip.extractall('gtfs/')

In [3]:
import boto3
import pandas as pd

In [4]:
gtfs_routes = pd.read_csv('gtfs/routes.txt')
gtfs_routes.head(3)

route_id agency_id route_short_name route_long_name  route_type  \
0         1    TRIMET                1         Vermont           3   
1         2    TRIMET              FX2        Division           3   
2         4    TRIMET                4       Fessenden           3   

                               route_url route_color route_text_color  \
0  https://trimet.org/schedules/r001.htm         NaN              NaN   
1  https://trimet.org/schedules/r002.htm      61A60E           FFFFFF   
2  https://trimet.org/schedules/r004.htm         NaN              NaN   

   route_sort_order  
0               400  
1               500  
2               600

In [5]:
gtfs_routes[['route_id','route_short_name','route_long_name']].to_json('gtfs/gtfs_routes.json',orient='records')

In [6]:
client = boto3.client("s3")
client.upload_file("gtfs/gtfs_routes.json", "meysohn-sandbox", "trimet_trip_planner/gtfs_routes.json",ExtraArgs={'ACL':'public-read'})

Make routes from `shapes.txt` file

In [7]:
gtfs_shapes = pd.read_csv('gtfs/shapes.txt')
gtfs_shapes.head(3)

shape_id  shape_pt_lat  shape_pt_lon  shape_pt_sequence  \
0    535813     45.522879   -122.677388                  1   
1    535813     45.522913   -122.677396                  2   
2    535813     45.522988   -122.677431                  3   

   shape_dist_traveled  
0                  0.0  
1                 12.6  
2                 41.3

In [33]:
gtfs_shapes['vertex_point'] = [Point(x, y) for x, y in zip(gtfs_shapes['shape_pt_lon'].to_numpy(),gtfs_shapes['shape_pt_lat'].to_numpy())]

/Users/benjaminmalnor/.pyenv/versions/miniconda3-latest/envs/geo-analysis/lib/python3.10/site-packages/pandas/core/dtypes/cast.py:127: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


Make shape vertices into shape lines

In [38]:
gtfs_shape_lines = gtfs_shapes.groupby('shape_id')[['vertex_point']].agg(lambda x: LineString(list(x))).reset_index()

In [40]:
gtfs_shape_lines_gdf = gpd.GeoDataFrame(gtfs_shape_lines, crs="EPSG:4326", geometry='vertex_point')
gtfs_shape_lines_gdf.head(3)

shape_id                                       vertex_point
0    535813  LINESTRING (-122.67739 45.52288, -122.67740 45...
1    535814  LINESTRING (-122.72189 45.47623, -122.72236 45...
2    535815  LINESTRING (-122.67586 45.52807, -122.67574 45...

In [41]:
gtfs_shape_lines_gdf.iloc[:10].explore()

In [43]:
gtfs_shape_lines_gdf.shape

(1004, 2)

In [8]:
gtfs_trips = pd.read_csv('gtfs/trips.txt')
gtfs_trips.head(3)

route_id service_id   trip_id  trip_short_name  direction_id  block_id  \
0         1      W.647  12336459              NaN             0      6174   
1         1      W.647  12336460              NaN             0      6470   
2         1      W.647  12336461              NaN             1      6169   

   shape_id  trip_type  wheelchair_accessible  
0    535813        NaN                      1  
1    535813        NaN                      1  
2    535814        NaN                      1

In [19]:
route_shapes = gtfs_trips.groupby(['route_id','shape_id']).agg(num_trips=('trip_id','nunique')).reset_index()
route_shapes.head(3)

route_id  shape_id  num_trips
0         1    535813          2
1         1    535814          2
2         1    537563          4

## How to handle multiple shapes per route. 
I'm thinking take union of shapes?

In [44]:
shapes_lines_w_route = gtfs_shape_lines_gdf.merge(route_shapes[['route_id','shape_id']], how='inner', on='shape_id')
shapes_lines_w_route.head(3)

shape_id                                       vertex_point  route_id
0    535813  LINESTRING (-122.67739 45.52288, -122.67740 45...         1
1    535814  LINESTRING (-122.72189 45.47623, -122.72236 45...         1
2    535815  LINESTRING (-122.67586 45.52807, -122.67574 45...         2

In [47]:
from shapely.ops import unary_union

In [50]:
shapes_lines_w_route.groupby('route_id').agg(shape_count=('shape_id','nunique')).reset_index().sort_values('shape_count', ascending=True)

route_id  shape_count
78        98            3
9         13            3
0          1            4
24        30            4
31        37            4
..       ...          ...
5          9           28
4          8           28
75        94           34
8         12           39
80       100           72

[94 rows x 2 columns]

In [51]:
shapes_lines_w_route_reduced = shapes_lines_w_route.groupby('route_id')[['vertex_point']].agg(lambda x: unary_union(x)).reset_index()

/Users/benjaminmalnor/.pyenv/versions/miniconda3-latest/envs/geo-analysis/lib/python3.10/site-packages/pandas/core/ops/array_ops.py:75: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = libops.scalar_compare(x.ravel(), y, op)


In [52]:
shapes_lines_w_route_reduced.columns

Index(['route_id', 'vertex_point'], dtype='object')

In [59]:
shapes_lines_w_route_reduced.set_geometry('vertex_point', inplace=True)
shapes_lines_w_route_reduced.set_crs("EPSG:4326", inplace=True)

route_id                                       vertex_point
0          1  MULTILINESTRING ((-122.67739 45.52288, -122.67...
1          2  MULTILINESTRING ((-122.67586 45.52807, -122.67...
2          4  MULTILINESTRING ((-122.67957 45.51475, -122.67...
3          6  MULTILINESTRING ((-122.69305 45.51762, -122.69...
4          8  MULTILINESTRING ((-122.67530 45.52776, -122.67...
..       ...                                                ...
89       200  MULTILINESTRING ((-122.68369 45.50962, -122.68...
90       203  MULTILINESTRING ((-122.80112 45.49062, -122.80...
91       208  MULTILINESTRING ((-122.68392 45.49950, -122.67...
92       290  MULTILINESTRING ((-122.63505 45.43074, -122.63...
93       291  MULTILINESTRING ((-122.67530 45.52776, -122.67...

[94 rows x 2 columns]

convert to trimet crs so we can simplify with accurate units

In [60]:
trimet_crs = "EPSG:2913"
shapes_lines_w_route_proj = shapes_lines_w_route_reduced.to_crs(trimet_crs)

In [78]:
shapes_lines_w_route_proj['simplified_lines'] = shapes_lines_w_route_proj['vertex_point'].simplify(500)

In [79]:
simply_lines_with_routes = shapes_lines_w_route_proj.set_geometry("simplified_lines").to_crs("EPSG:4326")

In [80]:
simply_lines_with_routes.explore()

In [81]:
simply_lines_with_routes_name = simply_lines_with_routes[['route_id','simplified_lines']].merge(gtfs_routes[['route_id','route_long_name']], how='inner', on='route_id')

In [82]:
simply_lines_with_routes_name.head(3)

route_id                                   simplified_lines route_long_name
0         1  MULTILINESTRING ((-122.67739 45.52288, -122.67...         Vermont
1         2  MULTILINESTRING ((-122.67586 45.52807, -122.67...        Division
2         4  MULTILINESTRING ((-122.67957 45.51475, -122.67...       Fessenden

In [83]:
simply_lines_with_routes_name.to_file("gis/export/simply_lines_with_routes_name.geojson", driver="GeoJSON")

In [86]:
for route_id in simply_lines_with_routes_name['route_id'].unique():
    one_route = simply_lines_with_routes_name[simply_lines_with_routes_name['route_id']==route_id].copy()
    one_route.to_file(f"gis/export/route_shapes/route_line_{route_id}.geojson", driver="GeoJSON")
    client = boto3.client("s3")
    client.upload_file(f"gis/export/route_shapes/route_line_{route_id}.geojson", "meysohn-sandbox", f"trimet_trip_planner/route_lines/route_line_{route_id}.geojson",ExtraArgs={'ACL':'public-read'})